In [1]:
# NumPy and odeint, our workhorses
import numpy as np
import scipy.integrate

# For interactive plots
import ipywidgets
import multiprocessing
import tqdm
# Plotting modules
import bokeh.io
import bokeh.plotting
from bokeh.models import Span

import matplotlib.pyplot as plt

# Ensure that plots show in the notebook
bokeh.io.output_notebook()


Bad key "text.kerning_factor" on line 4 in
/Users/haoran/opt/anaconda3/lib/python3.7/site-packages/matplotlib/mpl-data/stylelib/_classic_test_patch.mplstyle.
You probably need to get an updated matplotlibrc file from
https://github.com/matplotlib/matplotlib/blob/v3.1.3/matplotlibrc.template
or from the matplotlib source distribution


Loading BokehJS ...

In [2]:
# Column 0 is change in m, column 1 is change in p
simple_update = np.array([[1, 0],  
                          [-1, 0],  
                          [0, 1],  
                          [0, -1]], 
                         dtype=np.int)

In [3]:
def sample_discrete(probs):
    """Randomly sample an index with probability given by probs."""
    # Generate random number
    q = np.random.rand()
    
    # Find index
    i = 0
    p_sum = 0.0
    while p_sum < q:
        p_sum += probs[i]
        i += 1
    return i - 1

In [117]:
def activation_propensity(propensities, population, t, s_x,n_x,n_y,beta_y, beta_z, gamma,k_x):
    """Updates an array of propensities given a set of parameters
    and an array of populations.
    """
    # Unpack population
    x, y = population
    
    # Update propensities
    propensities[0] = beta_y * s_x / (1 + s_x) + 2
    propensities[1] = x           
    propensities[2] = gamma * (beta_z * (x/k_x)**n_y / (1 + (x/k_x)**n_y)) + 1
    propensities[3] = gamma * y   

In [5]:
def normalize(x):
    return (x - np.mean(x))/np.std(x)


def correlate(x, y, half=False):
    x = normalize(x)
    y = normalize(y)
    n = len(x)
    
    if n != len(y):
        raise RuntimeError('Can only correlate arrays of equal length.')
        
    if n % 2:
        lengths = np.concatenate((np.arange(n//2+1, n), np.arange(n, n//2, -1)))
        lags = np.concatenate((np.arange(-n//2+1, 0), np.arange(n//2+1)))
    else:
        lengths = np.concatenate((np.arange(n//2, n), np.arange(n, n//2, -1)))
        lags = np.concatenate((np.arange(-n//2, 0), np.arange(n//2)))
        
    # Compute correlation with max correlation being unity
    corr = np.correlate(x, y, 'same') / lengths
    corr /= corr.max()
    
    if half:
        return lags[n//2:], corr[n//2:]
    else:
        return lags, corr
    
    
def xcorr(x, y, normed=True, detrend=False, maxlags=20):
    # Cross correlation of two signals of equal length
    # Returns the coefficients when normed=True
    # Returns inner products when normed=False
    # Usage: lags, c = xcorr(x,y,maxlags=len(x)-1)
    # Optional detrending e.g. mlab.detrend_mean
    #x = normalize(x)
    #y = normalize(y)
    x = normalize(x)
    y = normalize(y)
    Nx = len(x)
    if Nx != len(y):
        raise ValueError('x and y must be equal length')
    
    if detrend:
        import matplotlib.mlab as mlab
        x = mlab.detrend_mean(np.asarray(x)) # can set your preferences here
        y = mlab.detrend_mean(np.asarray(y))
    
    c = np.correlate(x, y, mode='full')

    if normed:
        n = np.sqrt(np.dot(x, x) * np.dot(y, y)) # this is the transformation function
        c = np.true_divide(c,n)

    if maxlags is None:
        maxlags = Nx - 1

    if maxlags >= Nx or maxlags < 1:
        raise ValueError('maglags must be None or strictly '
                         'positive < %d' % Nx)

    lags = np.arange(-maxlags, maxlags + 1)
    c = c[Nx - 1 - maxlags:Nx + maxlags]
    return lags, c

In [6]:
def gillespie_draw(propensity_func, propensities, population, t, args=()):
    """
    Draws a reaction and the time it took to do that reaction.
    
    Parameters
    ----------
    propensity_func : function
        Function with call signature propensity_func(population, t, *args)
        used for computing propensities. This function must return
        an array of propensities.
    population : ndarray
        Current population of particles
    t : float
        Value of the current time.
    args : tuple, default ()
        Arguments to be passed to `propensity_func`.
        
    Returns
    -------
    rxn : int
        Index of reaction that occured.
    time : float
        Time it took for the reaction to occur.
    """
    # Compute propensities
    propensity_func(propensities, population, t, *args)
    
    # Sum of propensities
    props_sum = propensities.sum()
    
    # Compute next time
    time = np.random.exponential(1.0 / props_sum)
    
    # Compute discrete probabilities of each reaction
    rxn_probs = propensities / props_sum
    
    # Draw reaction from this distribution
    rxn = sample_discrete(rxn_probs)
    
    return rxn, time

In [7]:
def gillespie_ssa(propensity_func, update, population_0, time_points, args=()):
    """
    Uses the Gillespie stochastic simulation algorithm to sample
    from probability distribution of particle counts over time.
    
    Parameters
    ----------
    propensity_func : function
        Function of the form f(params, t, population) that takes the current
        population of particle counts and return an array of propensities
        for each reaction.
    update : ndarray, shape (num_reactions, num_chemical_species)
        Entry i, j gives the change in particle counts of species j
        for chemical reaction i.
    population_0 : array_like, shape (num_chemical_species)
        Array of initial populations of all chemical species.
    time_points : array_like, shape (num_time_points,)
        Array of points in time for which to sample the probability
        distribution.
    args : tuple, default ()
        The set of parameters to be passed to propensity_func.        

    Returns
    -------
    sample : ndarray, shape (num_time_points, num_chemical_species)
        Entry i, j is the count of chemical species j at time
        time_points[i].
    """

    # Initialize output
    pop_out = np.empty((len(time_points), update.shape[1]), dtype=np.int)

    # Initialize and perform simulation
    i_time = 1
    i = 0
    t = time_points[0]
    population = population_0.copy()
    pop_out[0,:] = population
    propensities = np.zeros(update.shape[0])
    while i < len(time_points):
        while t < time_points[i_time]:
            # draw the event and time step
            event, dt = gillespie_draw(propensity_func, propensities, population, t, args)
                
            # Update the population
            population_previous = population.copy()
            population += update[event,:]
                
            # Increment time
            t += dt

        # Update the index
        i = np.searchsorted(time_points > t, True)
        
        # Update the population
        pop_out[i_time:min(i,len(time_points))] = population_previous
        
        # Increment index
        i_time = i
                           
    return pop_out

In [129]:
a = 100


##Regime 1 

#Steady state


ccf_ss = []
cor_t_ss = []

args = (0, 4.0, 4.0, 8.0, 8.0, 1.0, 5.0)#(s_x,n_x,n_y,beta_y, beta_z, gamma,k_x)
time_points = np.linspace(0, 50, 101)
population_0 = np.array([2,1], dtype=int)
size = 100
for j in range(a):
    # Specify parameters for calculation

# Seed random number generator for reproducibility
#np.random.seed(43)

# Initialize output array
    samples = np.empty((size, len(time_points), 2), dtype=int)

# Run the calculations
    for i in tqdm.tqdm_notebook(range(size)):
        samples[i,:,:] = gillespie_ssa(activation_propensity, simple_update,
                                    population_0, time_points, args=args)
    

    cor_t = np.array([])
    ccf_ss.append(xcorr(samples[:,:,0].mean(axis=0), samples[:,:,1].mean(axis=0))[1])
    for i in range(time_points.shape[0]):
        cor_t = np.append(cor_t, np.corrcoef(samples[:,i,:][:,0], samples[:,i,:][:,1])[0,1])
    
    cor_t_ss.append(cor_t)





np.savetxt("cor_t_ss.csv", cor_t_ss, delimiter=",")
np.savetxt("ccf_ss.csv", ccf_ss, delimiter=",")



/Users/haoran/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


In [130]:
##Press perturbation



ccf_press_1 = []
cor_t_press_1 = []

args = (20, 4.0, 4.0, 8.0, 8.0, 1.0, 5.0)#(s_x,n_x,n_y,beta_y, beta_z, gamma,k_x)
time_points = np.linspace(0, 50, 101)
population_0 = np.array([2,1], dtype=int)
size = 100
for j in range(a):
    # Specify parameters for calculation

# Seed random number generator for reproducibility
#np.random.seed(43)

# Initialize output array
    samples = np.empty((size, len(time_points), 2), dtype=int)

# Run the calculations
    for i in tqdm.tqdm_notebook(range(size)):
        samples[i,:,:] = gillespie_ssa(activation_propensity, simple_update,
                                    population_0, time_points, args=args)
    

    cor_t = np.array([])
    ccf_press_1.append(xcorr(samples[:,:,0].mean(axis=0), samples[:,:,1].mean(axis=0))[1])
    for i in range(time_points.shape[0]):
        cor_t = np.append(cor_t, np.corrcoef(samples[:,i,:][:,0], samples[:,i,:][:,1])[0,1])
    
    cor_t_press_1.append(cor_t)



np.savetxt("cor_t_press_1.csv", cor_t_press_1, delimiter=",")
np.savetxt("ccf_press_1.csv", ccf_press_1, delimiter=",")






/Users/haoran/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:22: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


In [131]:
##Pulse perturbation



ccf_pulse_1 = []
cor_t_pulse_1 = []


size = 100
for j in range(a):
    # Specify parameters for calculation

# Seed random number generator for reproducibility
#np.random.seed(43)
    population_0 = np.array([2,1], dtype=int)
    args = (20, 4.0, 4.0, 8.0, 8.0, 1.0, 5.0)#(s_x,n_x,n_y,beta_y, beta_z, gamma,k_x)
    time_points = np.linspace(0, 25, 51)
# Initialize output array
    samples = np.empty((size, len(time_points), 2), dtype=int)

# Run the calculations
    for i in tqdm.tqdm_notebook(range(size)):
        samples[i,:,:] = gillespie_ssa(activation_propensity, simple_update,
                                    population_0, time_points, args=args)
        
    sample_1 = samples
    sample_2 = np.empty((size, len(time_points), 2), dtype=int)

    for k in range(size):
        population_0 = sample_1[k,50]
        args = (0, 4.0, 4.0, 8.0, 8.0, 1.0, 5.0)#(s_x,n_x,n_y,beta_y, beta_z, gamma,k_x)
        time_points = np.linspace(0, 25, 51)
        size_0 = 1
        samples = np.empty((size_0, len(time_points), 2), dtype=int)

        for i in tqdm.tqdm_notebook(range(size_0)):
            samples[i,:,:] = gillespie_ssa(activation_propensity, simple_update,
                                    population_0, time_points, args=args)    
    

        sample_2[k] = samples[0]
    
    
    samples = np.delete(np.concatenate((sample_1,sample_2),axis = 1), 51,axis= 1)


    cor_t = np.array([])
    ccf_pulse_1.append(xcorr(samples[:,:,0].mean(axis=0), samples[:,:,1].mean(axis=0))[1])
    for i in range(2* time_points.shape[0]-1):
        cor_t = np.append(cor_t, np.corrcoef(samples[:,i,:][:,0], samples[:,i,:][:,1])[0,1])
    
    cor_t_pulse_1.append(cor_t)

np.savetxt("cor_t_pulse_1.csv", cor_t_pulse_1, delimiter=",")
np.savetxt("ccf_pulse_1.csv", ccf_pulse_1, delimiter=",")





/Users/haoran/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:22: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


/Users/haoran/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:36: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


In [132]:
#Regime 2

##Press perturbation



ccf_press_2 = []
cor_t_press_2 = []

args = (1, 4.0, 4.0, 8.0, 8.0, 1.0, 5.0)#(s_x,n_x,n_y,beta_y, beta_z, gamma,k_x)
time_points = np.linspace(0, 50, 101)
population_0 = np.array([2,1], dtype=int)
size = 100
for j in range(a):
    # Specify parameters for calculation

# Seed random number generator for reproducibility
#np.random.seed(43)

# Initialize output array
    samples = np.empty((size, len(time_points), 2), dtype=int)

# Run the calculations
    for i in tqdm.tqdm_notebook(range(size)):
        samples[i,:,:] = gillespie_ssa(activation_propensity, simple_update,
                                    population_0, time_points, args=args)
    

    cor_t = np.array([])
    ccf_press_2.append(xcorr(samples[:,:,0].mean(axis=0), samples[:,:,1].mean(axis=0))[1])
    for i in range(time_points.shape[0]):
        cor_t = np.append(cor_t, np.corrcoef(samples[:,i,:][:,0], samples[:,i,:][:,1])[0,1])
    
    cor_t_press_2.append(cor_t)



np.savetxt("cor_t_press_2.csv", cor_t_press_2, delimiter=",")
np.savetxt("ccf_press_2.csv", ccf_press_2, delimiter=",")






/Users/haoran/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:24: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


In [133]:
##Pulse perturbation

ccf_pulse_2 = []
cor_t_pulse_2 = []


size = 100
for j in range(a):
    # Specify parameters for calculation

# Seed random number generator for reproducibility
#np.random.seed(43)
    population_0 = np.array([2,1], dtype=int)
    args = (1, 4.0, 4.0, 8.0, 8.0, 1.0, 5.0)#(s_x,n_x,n_y,beta_y, beta_z, gamma,k_x)
    time_points = np.linspace(0, 25, 51)
# Initialize output array
    samples = np.empty((size, len(time_points), 2), dtype=int)

# Run the calculations
    for i in tqdm.tqdm_notebook(range(size)):
        samples[i,:,:] = gillespie_ssa(activation_propensity, simple_update,
                                    population_0, time_points, args=args)
        
    sample_1 = samples
    sample_2 = np.empty((size, len(time_points), 2), dtype=int)

    for k in range(size):
        population_0 = sample_1[k,50]
        args = (0, 4.0, 4.0, 8.0, 8.0, 1.0, 5.0)#(s_x,n_x,n_y,beta_y, beta_z, gamma,k_x)
        time_points = np.linspace(0, 25, 51)
        size_0 = 1
        samples = np.empty((size_0, len(time_points), 2), dtype=int)

        for i in tqdm.tqdm_notebook(range(size_0)):
            samples[i,:,:] = gillespie_ssa(activation_propensity, simple_update,
                                    population_0, time_points, args=args)    
    

        sample_2[k] = samples[0]
    
    
    samples = np.delete(np.concatenate((sample_1,sample_2),axis = 1), 51,axis= 1)


    cor_t = np.array([])
    ccf_pulse_2.append(xcorr(samples[:,:,0].mean(axis=0), samples[:,:,1].mean(axis=0))[1])
    for i in range(2*time_points.shape[0]-1):
        cor_t = np.append(cor_t, np.corrcoef(samples[:,i,:][:,0], samples[:,i,:][:,1])[0,1])
    
    cor_t_pulse_2.append(cor_t)

np.savetxt("cor_t_pulse_2.csv", cor_t_pulse_2, delimiter=",")
np.savetxt("ccf_pulse_2.csv", ccf_pulse_2, delimiter=",")


/Users/haoran/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:20: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


/Users/haoran/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:34: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
